# Premiers pas avec la Microlabbox
::: danger Avertissement
Ce guide a pour but d'initier au pilotage d'un équipement physique à l'aide de la Microlabbbox. Ces étapes doivent être scrupuleusement suivies. En cas de mauvaise manipulation, un danger pour le matériel et les personnes est possible.

Exécuter ce tutoriel uniquement avec l'autorisation et sous la supervision de votre encadrant.
:::

# Objectif du tutoriel #
Ce tutoriel va permettre de se familiariser "pas à pas" avec les différentes étapes d'un projet HIL.
L'objectif est le **pilotage de l'alimentation DC réversible** (PSB E9000) à l'aide de la **Microlabbox** par protocole de communication **CANopen**.

Les étapes successives abordées sont:

1. Modélisation dans Simulink.
2. Compilation avec Real-Time Interface (RTI).
3. Téléchargement dans la MicroLabBox.
4. Exécution temps réel du code.
5. Supervision avec ControlDesk : visualisation et interaction en direct.

Avant de débuter ce tutoriel, l'utilisateur s'est assuré que :
- Matlab dispose des modules RTI nécessaires
- la Microlabbox est correctement connectée au réseau Ethernet et sous tension
- l'alimentation DC (PSB E9000) est alimentée en triphasée et sous tension
- l'alimentation DC est reliée à la Microlabbox par bus CAN (en respectant les impédances de terminaison 120 $\Omega$ du bus)

::: warning Avertissement
Par précaution, aucune charge électrique ne sera reliée à la sortie de l'alimentation DC.
:::

## Modélisation dans Simulink ##

### Vérification de la configuration minimale du contrôleur ###
La MicroLabBox de dSPACE permet de contrôler un réseau CAN via le protocole CANOpen. Pour cela, deux toolboxes sont nécessaires :

- dSPACE CANOpen Master Blockset
- dSPACE RTI CAN MultiMessage Blockset

Via le ***RTICANMM ControllerSetup***, le connecteur CAN de la MicroLabBox peut être configuré ou non avec une résistance de terminaison de 120 Ohm. Si oui, l’équipement peut être en bout du réseau CAN.

Pour générer et configurer le connecteur CANOpen de la MicroLabBox, il faut tout d’abord s’assurer de la présence du RTI data adapté à celle-ci : ***DS1202***.
Ce bloc est créé automatiquement quand un nouveau modèle RTI1202 est généré.

 1. Créer un dossier racine dans lequel tous les fichiers seront créés (ex: `Work(D:)\projet_initiation_microlabbox\`)
 2. Lancer matlab puis Simulink
 3. Modifier le dossier de travail (`D:\projet_initiation_microlabbox`)

 ### Création d'un nouveau projet ###
1. Faire `New->Project->Blank project`
2. Rentrer le nom du projet (ex: Project name: `TUTO_projet_Simulink`), le chemin d'accès puis cliquer sur __Create__.
3. Lancer Simulink (à l'aide du menu HOME->Simulink ou en tapant `simulink` dans la fenêtre __Command Window__  puis Entrée)
4. Sélectionner le template **RTI1202**

```{dropdown} Template RTI1202
:open: false

<img src="../../_static/figures/template_RTI1202.PNG" alt="drop & drag slx to prj" width="90%" class="center-img">
```

A la création du projet, seul le bloc __RTI Data__ apparaît.

In [2]:
from IPython.display import HTML
HTML('<img src="../../_static/figures/RTI_data.PNG" alt="RTI_data.PNG" width="10%"')

Ce bloc est utilisé par RTI pour stocker des données internes dépendantes du modèle. Veuillez conserver ce bloc au niveau de la racine du modèle (ne pas mettre dans un sous-bloc). La suppression de ce bloc entraînera une perte de données.

::: danger Avertissement
Ne jamais supprimer ce bloc ou le copier dans un autre projet!
:::

5. Vérifier les paramètres de simulation (Ctrl+E). Dans le menu __Code Generation__, vérifier que `rti1202.tlc` apparaît dans le champ `System target file`
6. Enregistrer le modèle simulink dans le dossier créé (ex: `D:\projet_initiation_microlabbox`)
7. Le modèle simulink vierge est créé mais doit être ajouté au projet. Pour cela il suffit de faire un __Drag & Drop__ du fichier simulink dans la fenêtre project comme illustré ci-dessous.

```{dropdown} Drag & drop Simulink
:open: false

<img src="../../_static/figures/simulink_to_project.png" alt="drop & drag slx to prj" width="90%" class="center-img">
```

::: tip Conseil
Pour tout fichier matlab nécessaire au projet, penser à associer les fichiers .m au projet en procédant comme précédemment.
:::

### Ajouter et configurer les toolbox ###

8. Ajouter les blocs simulink nécessaires à la communication CANopen. Ouvrir __Library Browser__ du menu __SIMULATION__ de Simulink et ajouter les blocs de la librairie Dspace suivants:
- CANOpen Master Blockset ->CANopen Setup
- RTI CAN MultiMessage Blockset -> RTICANMM Controller Setup
- RTI CAN MultiMessage Blockset -> RTICANMM General Setup

```{dropdown} Library Browser
:open: false

<img src="../../_static/figures/library_browser.PNG" alt="library_browser" width="90%" class="center-img">
```

#### Bloc RTI CAN MultiMessage Setup ####

9. Double cliquer sur le bloc **RTI CAN MultiMessage Setup - General Setup**, pour obtenir la fenêtre suivante:

```{dropdown} RTI CAN MultiMessage Setup
:open: false

<img src="../../_static/figures/bloc_RTIcan_generalsetup.PNG" alt="bloc RTIcan generalsetup" width="50%" class="center-img">
```

Ce bloc permet de définir le dossier dans lequel l'ensemble des fichiers générés seront enregistrés. Par défaut, le dossier est nommé __RTICANMM_FILES__. Vérifier que le __Model root__ s'adresse correctement au dossier de votre projet. Puis __OK__.

#### Bloc RTI CAN ControllerSetup ####

10. Double cliquer sur le bloc **RTI CAN ControllerSetup**, pour obtenir la fenêtre suivante:

```{dropdown} RTIcan Controller Setup
:open: false

<img src="../../_static/figures/bloc_RTIcan_controllersetup.PNG" alt="bloc RTIcan controllersetup" width="50%" class="center-img">
```

Ce bloc permet de configurer un contrôleur CAN en définissant les paramètres de communication du bus CAN pour que le reste du modèle Simulink puisse envoyer et recevoir des messages CAN en temps réel.

11. Régler la vitesse de communication à `250 Kb/s` puis __Apply__.

### Création d'un noeud ###
Le troisième bloc permet de créer les différents noeuds (équipements reliés au bus CAN).

Le bloc CANopen Setup sert à :
- Initialiser la couche CANopen sur le matériel dSPACE
- Définir les paramètres de base du réseau CANopen
- Permettre l'utilisation des blocs CANopen dans le modèle

Dans ce tutoriel, un seul noeud est requis (l'alimentation DC PSBE 9000).

12. Double cliquer sur le bloc **CANopen Setup**, pour obtenir la fenêtre suivante:

```{dropdown} bloc CANopen Setup
:open: false

<img src="../../_static/figures/bloc_CANopen_Setup.PNG" alt="bloc CANopen Setup" width="50%" class="center-img">
```

Cette fenêtre comporte 3 menus dans la colonne de gauche:
- General Setup
- Nodes
- Synch block

13. Sélectionner __Nodes__. Indiquer le numéro du noeud de l'équipement à définir.

::: tip Conseil
Le numéro ID des équipements est directement configuré sur les appareils. L'alimentation DC PSBE 9000 est déclarée comme étant le noeud **2**.
Pour vérifier la configuration de l'alimentation, suivre les consignes [configuration ID de l'alimentation](ID_alim).
:::

Dans __Select nodes__, indiquer `2` puis __add to model__. __Node 2__ apparaît dans la colonne de gauche.
14. Cliquer sur le noeud créé.
Les menus **General** et **Advanced** apparaissent.



Le menu général permet de configurer: 
-	Le numéro du nœud
-	Le nombre de RxPDO souhaité
-	Le nombre de TxPDO souhaité

```{dropdown} Canopen Setup
:open: false

<div style="display: flex; gap: 10px; justify-content: space-between;">
  <img src="../../_static/figures/bloc_CANopen_Setup_node_general.PNG" alt="bloc CANopen Setup node General" width="48%">
  <img src="../../_static/figures/bloc_CANopen_Setup_node_advanced.PNG" alt="bloc CANopen Setup node Advanced" width="48%">
</div>
```

::: warning Avertissement
Il est important de sélectionner __No boot-up message expected__ pour l'alimentation DC qui ne génère pas de message de démarrage.
:::

15. Cliquer sur Synch block et indiquer un __Time period for syncrhonization message [s]__ de `0.5`.
16. Cliquer sur le bouton `Create`. Le modèle simulink crée un bloc noeud comme illustré ci-dessous.

```{dropdown} Bloc noeud Créé
:open: false

<img src="../../_static/figures/noeud_cree.PNG" alt="noeud cree" width="50%">
```

Ce bloc affiche toutes les entrées et les sorties pour intéragir avec le noeud 2 en temps-réel.

::: tip Conseil
Pour connaître la définition des différentes entrées et sorties, voir [Définition des E/S node bloc](definition_simulink_node_bloc).
:::

A présent que le noeud est créé, il faut compléter ses entrées et sorties pour permettre l'envoi et la réception de messages à l'équipement via le bus CAN.
Ces messages, codés en hexadécimal, obéissent à un format standardisé en partie (ex: VendorName ou ProductNumber). D'autres sont modifiables par le fabricant et spécifiques à chaque équipement.

Pour connaître l'ensemble de ces paramètres de réglage et de communication, les équipements communicants possèdent un fichier **EDS** (Electronic Data Sheet) qui décrit les différents registres de l'équipement, les valeurs associées.

Le fichier **EDS** de l'alimentation DC est consultable sur le lien suivant [Fichier EDS](lecture_fichier_eds).

::: tip Conseil
Pour faciliter la lecture des fichiers EDS, vous pouvez utiliser le logiciel Vector téléchargeable ici [Vector EDS](../../5_%20Ressources%20logicielles/Vector/CANeds.zip).
:::

## Exemple de modèle Simulink de contrôle de l'alimentation DC ##

```{dropdown} Modèle Simulink - Contrôle Alimentation DC
:open: false

<img src="../../_static/figures/modele_simulink_complet.PNG" alt="modele alimentation DC" width="100%" class="center-img">
```

## Compilation avec Real-Time Interface ##

## Téléchargement dans la Microlabbox ##

## Exécution temps-réel du code ##

## Supervision avec ControlDesk ##